# Flappy Bird AI Capstone Project - Coding Path (Advanced Skeleton)

Welcome to the advanced skeleton notebook for the Flappy Bird AI Capstone Project. This notebook is designed to guide you through key components of the coding path. Follow the hints and placeholders provided to complete the implementation.

In [2]:
# Install essential libraries for the project
%pip install numpy tensorflow keras gym pygame opencv-python
%pip install git+https://github.com/ntasfi/PyGame-Learning-Environment.git
%pip install ple


Note: you may need to restart the kernel to use updated packages.
  Cloning https://github.com/ntasfi/PyGame-Learning-Environment.git to c:\users\hisha\appdata\local\temp\pip-req-build-20nhqps_
  Resolved https://github.com/ntasfi/PyGame-Learning-Environment.git to commit 3dbe79dc0c35559bb441b9359948aabf9bb3d331
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
Note: you may need to restart the kernel to use updated packages.


  Running command git clone --filter=blob:none --quiet https://github.com/ntasfi/PyGame-Learning-Environment.git 'C:\Users\hisha\AppData\Local\Temp\pip-req-build-20nhqps_'


Note: you may need to restart the kernel to use updated packages.


In [3]:
import os
import urllib.request
import zipfile
from ple import PLE
from ple.games.flappybird import FlappyBird
import pygame

# Direct link to the master branch ZIP of the PLE repo
repo_url = 'https://github.com/ntasfi/PyGame-Learning-Environment/archive/master.zip'
zip_path = 'ple/games/flappybird/assets_temp.zip'
assets_dir = 'ple/games/flappybird/assets'

# Only download and extract if assets directory is missing
if not os.path.exists(assets_dir):
    # Ensure the parent directories exist
    os.makedirs('ple/games/flappybird', exist_ok=True)

    # Download the repository as a ZIP file
    urllib.request.urlretrieve(repo_url, zip_path)

    # Extract only the assets for FlappyBird
    with zipfile.ZipFile(zip_path, 'r') as zip_ref:
        # Identify all members that belong to the FlappyBird assets directory
        members = [
            m for m in zip_ref.namelist() 
            if m.startswith('PyGame-Learning-Environment-master/ple/games/flappybird/assets/')
        ]

        for member in members:
            # Compute the relative path inside flappybird directory
            relative_path = member.replace('PyGame-Learning-Environment-master/ple/games/flappybird/', '')
            if not relative_path:
                continue  # Skip the top-level directory

            target_path = os.path.join('ple/games/flappybird', relative_path)

            # Check if this member is a directory
            if member.endswith('/'):
                # Create the directory if it doesn't exist
                os.makedirs(target_path, exist_ok=True)
            else:
                # It's a file; first ensure the parent directory exists
                os.makedirs(os.path.dirname(target_path), exist_ok=True)
                # Extract the file
                with zip_ref.open(member) as source, open(target_path, 'wb') as target:
                    target.write(source.read())

    # Remove the temporary ZIP file after extraction
    os.remove(zip_path)


pygame 2.6.1 (SDL 2.28.4, Python 3.11.9)
Hello from the pygame community. https://www.pygame.org/contribute.html
couldn't import doomish
Couldn't import doom


In [4]:
# Import necessary modules
from ple import PLE
from ple.games.flappybird import FlappyBird
import pygame
import os
import urllib.request
import zipfile

# Download and extract the assets if not already done
assets_url = 'https://github.com/ntasfi/PyGame-Learning-Environment/tree/master/ple/games/flappybird/assets'
assets_path = 'ple/games/flappybird/assets'
assets_dir = 'ple/games/flappybird/assets'

if not os.path.exists(assets_dir):
    urllib.request.urlretrieve(assets_url, assets_path)
    with zipfile.ZipFile(assets_path, 'r') as zip_ref:
        zip_ref.extractall('ple/games/flappybird/')
    os.remove(assets_path)

In [5]:
import ple
print(ple.__file__)


C:\Users\hisha\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\ple\__init__.py


In [6]:
# Initialize the Flappy Bird game
game = FlappyBird()

# Set up PLE with the game
p = PLE(game, fps=30, display_screen=True)
p.init()

# Test the updated game environment
running = True
while running:
    if p.game_over():
        p.reset_game()

    # Perform a no-operation action to test the game
    p.act(p.NOOP)

    # Handle pygame events for window management
    for event in pygame.event.get():
        if event.type == pygame.QUIT:
            running = False

pygame.quit()

## Pre-trained Model Integration

In [7]:
# Step 1: Load the Pre-trained MobileNetV2 Model
from tensorflow.keras.applications import MobileNetV2
from tensorflow.keras.models import Model
from tensorflow.keras.layers import GlobalAveragePooling2D, Dense

# Load the base MobileNetV2 model without the top layers
base_model = MobileNetV2(weights='imagenet', include_top=False, input_shape=(224, 224, 3))

# Freeze the base model layers to prevent them from being updated during training
for layer in base_model.layers:
    layer.trainable = False

# Add custom layers for the Q-network
x = GlobalAveragePooling2D()(base_model.output)
x = Dense(128, activation='relu')(x)  # Custom dense layer
output = Dense(2, activation='linear')(x)  # Output layer for actions (e.g., flap or no-flap)

# Combine the base model and custom layers
model = Model(inputs=base_model.input, outputs=output)

# Compile the model
model.compile(optimizer='adam', loss='mse')
print('Model successfully loaded and modified.')

Model successfully loaded and modified.


## Integrating the Model with the Game Environment

In [8]:
# Example function to preprocess game frames
import cv2
import numpy as np

def preprocess_frame(frame):
    frame = cv2.resize(frame, (224, 224))  # Resize to match input shape
    frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)  # Convert to RGB
    frame = frame / 255.0  # Normalize pixel values
    return np.expand_dims(frame, axis=0)  # Add batch dimension

# Initialize the Flappy Bird game
game = FlappyBird()
p = PLE(game, fps=30, display_screen=False)
p.init()

# Capture a sample frame from the game
p.reset_game()
sample_frame = p.getScreenRGB()

# Predict action for a sample frame
preprocessed_frame = preprocess_frame(sample_frame)
action_values = model.predict(preprocessed_frame)
chosen_action = np.argmax(action_values)
print(f'Chosen action: {chosen_action}')

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step
Chosen action: 0


## Reinforcement Learning Implementation

In [9]:
# Step 2: Implement the DQNAgent Class
import numpy as np
from collections import deque

class DQNAgent:
    def __init__(self, state_size, action_size):
        self.state_size = state_size
        self.action_size = action_size
        self.memory = deque(maxlen=2000)  # Replay memory
        self.gamma = 0.95  # Discount factor
        self.epsilon = 1.0  # Exploration rate
        self.epsilon_min = 0.01  # Minimum exploration rate
        self.epsilon_decay = 0.995  # Exploration decay rate
        self.model = self._build_model()
    
    def _build_model(self):
        """Build the Q-network using the pre-trained model."""
        from tensorflow.keras.models import Model
        from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
        from tensorflow.keras.applications import MobileNetV2

        # Load the base MobileNetV2 model without the top layers
        base_model = MobileNetV2(weights='imagenet', include_top=False, input_shape=(224, 224, 3))
        for layer in base_model.layers:
            layer.trainable = False

        # Add custom layers for Q-value prediction
        x = GlobalAveragePooling2D()(base_model.output)
        x = Dense(128, activation='relu')(x)
        output = Dense(self.action_size, activation='linear')(x)
        
        model = Model(inputs=base_model.input, outputs=output)
        model.compile(optimizer='adam', loss='mse')
        return model
    
    def remember(self, state, action, reward, next_state, done):
        """Store experiences in replay memory."""
        self.memory.append((state, action, reward, next_state, done))

    def act(self, state):
        """Choose an action based on epsilon-greedy policy."""
        if np.random.rand() <= self.epsilon:
            return np.random.choice(self.action_size)  # Explore
        q_values = self.model.predict(state)
        return np.argmax(q_values[0])  # Exploit

    def replay(self, batch_size):
        """Train the model using random samples from memory."""
        if len(self.memory) < batch_size:
            return
        minibatch = np.random.choice(len(self.memory), batch_size, replace=False)
        for i in minibatch:
            state, action, reward, next_state, done = self.memory[i]
            target = reward
            if not done:
                target += self.gamma * np.amax(self.model.predict(next_state)[0])
            target_f = self.model.predict(state)
            target_f[0][action] = target
            self.model.fit(state, target_f, epochs=1, verbose=0)

    def update_epsilon(self):
        """Decay the exploration rate."""
        if self.epsilon > self.epsilon_min:
            self.epsilon *= self.epsilon_decay

## Model Training

In [12]:
from tqdm import tqdm
import numpy as np
import cv2

# Define the preprocess function
def preprocess(state):
    """Preprocess game frames for the model."""
    state = cv2.resize(state, (224, 224))  # Resize to match input shape
    state = cv2.cvtColor(state, cv2.COLOR_BGR2RGB)  # Convert to RGB
    state = state / 255.0  # Normalize pixel values
    return np.expand_dims(state, axis=0)  # Add batch dimension

# Initialize the DQNAgent
state_size = (224, 224, 3)
action_size = 2  # Number of possible actions (e.g., flap or no-flap)
agent = DQNAgent(state_size, action_size)

# Initialize training parameters
n_episodes = 50
batch_size = 15

# Initialize the Pygame display
pygame.init()
screen = pygame.display.set_mode((1, 1))

# Training Loop
for episode in tqdm(range(n_episodes)):
    # Reset the environment and get the initial state
    p.reset_game()
    pygame.event.pump()  # Ensure the game screen is rendered
    state = preprocess(p.getScreenRGB())

    done = False
    total_reward = 0  # Track cumulative reward per episode

    while not done:
        # Handle pygame events for window management
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                done = True
                break

        if done:
            break

        # Select an action
        action = agent.act(state)

        # Perform the action and observe the next state and reward
        reward = p.act(action)
        pygame.event.pump()  # Ensure the game screen is rendered
        next_state = preprocess(p.getScreenRGB())
        done = p.game_over()

        # Store the experience in memory
        agent.remember(state, action, reward, next_state, done)

        # Move to the next state
        state = next_state
        total_reward += reward

        # Train the model if enough samples are in memory
        if len(agent.memory) > batch_size:
            agent.replay(batch_size)

    # Update exploration rate (epsilon)
    agent.update_epsilon()

    # Log performance metrics
    print(f"Episode {episode + 1}/{n_episodes} - Total Reward: {total_reward} - Epsilon: {agent.epsilon:.2f}")

    # Save model checkpoint every 50 episodes
    if (episode + 1) % 50 == 0:
        agent.model.save(f"dqn_flappybird_episode_{episode + 1}.h5")

# Quit Pygame
pygame.quit()

  0%|          | 0/50 [00:00<?, ?it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━

  2%|▏         | 1/50 [00:23<19:20, 23.69s/it]

Episode 1/50 - Total Reward: -5.0 - Epsilon: 0.99
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 55ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 87ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step


  4%|▍         | 2/50 [01:41<44:11, 55.23s/it]

...

Episode 48/50 - Total Reward: -5.0 - Epsilon: 0.79
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step

 98%|█████████▊| 49/50 [57:36<01:09, 69.78s/it]

Episode 49/50 - Total Reward: -5.0 - Epsilon: 0.78
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step

Episode 50/50 - Total Reward: -5.0 - Epsilon: 0.78


100%|██████████| 50/50 [58:45<00:00, 70.52s/it]


## Testing and Evaluation

In [24]:
import numpy as np
import cv2
import pygame  # Import Pygame
from ple import PLE
from ple.games.flappybird import FlappyBird

# Initialize the game and PLE
game = FlappyBird()
p = PLE(game, fps=30, display_screen=True)
p.init()

# Disable exploration for testing
agent.epsilon = 0  # Disable exploration

def preprocess(state):
    """Prepare game frames for evaluation."""
    state = cv2.resize(state, (224, 224))  # Resize to match input shape
    state = cv2.cvtColor(state, cv2.COLOR_BGR2RGB)  # Convert to RGB
    state = state / 255.0  # Normalize pixel values
    return np.expand_dims(state, axis=0)  # Add batch dimension

# Initialize Pygame
pygame.init()

# Set up the display surface
screen = pygame.display.set_mode((288, 512))  # Use the game's window size

for episode in range(10):
    p.reset_game()
    pygame.event.pump()  # Update the game screen
    state = preprocess(p.getScreenRGB())
    done = False
    total_reward = 0

    while not done:
        # Handle Pygame events to keep the window responsive
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                done = True
                break

        # Choose an action using the trained policy
        action = agent.act(state)

        # Execute the chosen action
        reward = p.act(action)
        pygame.event.pump()  # Update the game screen
        next_state = preprocess(p.getScreenRGB())
        done = done or p.game_over()
        total_reward += reward
        state = next_state

    print(f'Episode {episode + 1}: Total Reward = {total_reward}')

# Quit Pygame after all episodes
pygame.quit()

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━